In [8]:
import json
import requests
import sys
from datetime import datetime, time

sys.path.insert(0, '../../../commons/')


from virasana.integracao.due import raspa_due

VIRASANA_URL = "http://localhost/virasana/"
VIRASANA_URL = "http://10.68.64.12/virasana/"

## Realizando consulta no MongoDB Gridfs do AJNA via API virasana

In [11]:
diaapesquisar = datetime.today()
diaapesquisar = datetime(2019, 10, 1)

In [12]:
datainicial = datetime.strftime(datetime.combine(diaapesquisar, time.min), '%Y-%m-%d  %H:%M:%S')
datafinal = datetime.strftime(datetime.combine(diaapesquisar, time.max), '%Y-%m-%d %H:%M:%S')
print(datainicial, datafinal)

2019-10-01  00:00:00 2019-10-01 23:59:59


In [13]:
params = {'query': 
          { 'metadata.dataescaneamento': {'$gte': datainicial, '$lte': datafinal},
            'metadata.contentType': 'image/jpeg',
            'metadata.carga.manifesto.tipomanifesto': 'lce'
          },
          'projection': 
          {'metadata.numeroinformado': 1,
           'metadata.dataescaneamento': 1}
         }

r = requests.post(VIRASANA_URL + "grid_data", json=params)
lista_lce = list(r.json())
print(len(lista_lce))

params['query']['metadata.carga.manifesto.tipomanifesto'] = None
r = requests.post(VIRASANA_URL + "grid_data", json=params)
lista_null = list(r.json())
print(len(lista_null))

# print(r.url)
# print(r.text)

45
1368


In [14]:
lista_lce

[{'_id': '5d94bbd39616ee69f69ace8b',
  'metadata': {'dataescaneamento': '2019-10-01 00:35:56',
   'numeroinformado': 'MSKU0103025'}},
 {'_id': '5d94bbfa9616ee69f69ad231',
  'metadata': {'dataescaneamento': '2019-10-01 01:48:53',
   'numeroinformado': 'TEMU9628143'}},
 {'_id': '5d94bc3c07eed8ce37dae2a6',
  'metadata': {'dataescaneamento': '2019-10-01 03:06:06',
   'numeroinformado': 'HASU4504984'}},
 {'_id': '5d94bc3d07eed8ce37dae2e6',
  'metadata': {'dataescaneamento': '2019-10-01 03:18:28',
   'numeroinformado': 'MSKU8203139'}},
 {'_id': '5d94bc3c07eed8ce37dae2be',
  'metadata': {'dataescaneamento': '2019-10-01 03:39:35',
   'numeroinformado': 'MRKU6003377'}},
 {'_id': '5d94bc5e9616ee69f69ad674',
  'metadata': {'dataescaneamento': '2019-10-01 03:46:34',
   'numeroinformado': 'MRKU6361010'}},
 {'_id': '5d94bc5e9616ee69f69ad684',
  'metadata': {'dataescaneamento': '2019-10-01 03:53:13',
   'numeroinformado': 'SZLU9465887'}},
 {'_id': '5d94bc5e9616ee69f69ad65c',
  'metadata': {'dataescan

In [30]:
# lista = [['MSCU6656780', '']]
lista = lista_null # [*lista_lce, *lista_null]
conteineres_ids = {linha['metadata']['numeroinformado']: linha['_id'] for linha in lista}
conteineres = list(conteineres_ids.keys())

print(conteineres_ids)


{'ERRO': '5d94be0a9616ee69f69b0112', 'MRSU3984791': '5d94bbcb9616ee69f69acd0a', 'CXDU2012450': '5d94bbaf9616ee69f69acc43', 'SUDU7933563': '5d94bbf19616ee69f69ad046', 'TCLU4044495': '5d94bbcd9616ee69f69acd62', 'HLBU1686158': '5d94bbaf9616ee69f69acc4f', 'MSCU4872203': '5d94bbcd9616ee69f69acd66', 'MSKU2908142': '5d94bbb09616ee69f69acc87', 'HLXU8740392': '5d94bbaf9616ee69f69acc57', 'EXFU8106262': '5d94bbcd9616ee69f69acd6a', 'MEDU5443452': '5d94bbb09616ee69f69acc6b', 'MSKU5877976': '5d94bbb09616ee69f69acc8f', 'APZU3610264': '5d94bc4107eed8ce37dae418', 'TRLU7056694': '5d94bbb09616ee69f69acc9b', 'TRLU7508433': '5d94bc4307eed8ce37dae499', 'HLBU9072921': '5d94bbaf9616ee69f69acc53', 'TTNU3703788': '5d94bc4307eed8ce37dae49e', 'TCLU1024005': '5d94bbcc9616ee69f69acd26', 'FCIU3623386': '5d94bc4207eed8ce37dae43f', 'MSDU7375117': '5d94bbb09616ee69f69acc7f', 'BSIU9278129': '5d94bbd29616ee69f69ace5b', 'HLBU1062275': '5d94bbd29616ee69f69ace6b', 'MSCU7479946': '5d94bbd19616ee69f69ace27', 'MEDU6745586': '5

## Conectar na API do Pucomex/suiterfb para encontrar e baixar DUE 

In [31]:
%%time
from selenium import webdriver

GECKO_PATH = 'C:\\Users\\25052288840\\Downloads\\chromedriver.exe'
driver = webdriver.Chrome(GECKO_PATH)
raspa_due.auth_suite_rfb(driver)
try:
    %time conteineres_listadue = raspa_due.get_dues_pos_acd(driver, conteineres)
    # print(conteineres_listadue)
    %time due_detalhe = raspa_due.detalha_dues(driver, conteineres_listadue)
    # print(conteineres_due)
finally:
    driver.close()

    

Wall time: 12min 34s
Wall time: 6min 52s
Wall time: 19min 43s


## Conectar na API do virasana para fazer UPLOAD do arquivo JSON resultante

O arquivo seguirá o formato [{_id: {Documento DUE}}]

In [32]:
print(len(conteineres_listadue))
print(len(due_detalhe))

1338
320


In [33]:
for conteiner, dues in list(conteineres_listadue.items())[:40]:
    if dues is not None and len(dues) > 0:
        print(conteiner, dues)
        
for due, conteudo in list(due_detalhe.items())[:10]:
    print(due, json.dumps(conteudo)[:30])

MRSU3984791 ['19BR0013347623']
CXDU2012450 ['19BR0012290946']
SUDU7933563 ['19BR0013033432']
HLBU1686158 ['19BR0013305408']
MSKU2908142 ['19BR0013246363']
HLXU8740392 ['19BR0013093869']
MEDU5443452 ['19BR0013166971']
MSKU5877976 ['19BR0013246363']
TRLU7056694 ['19BR0013318836']
HLBU9072921 ['19BR0013349413']
TCLU1024005 ['19BR0013307540']
MSDU7375117 ['19BR0013316698']
BSIU9278129 ['19BR0013302298']
HLBU1062275 ['19BR0013313834']
MEDU6745586 ['19BR0013269827']
BMOU9200737 ['19BR0013359559']
MRSU3274320 ['19BR0013491970']
SEGU9666403 ['19BR0013233687']
MRKU0349357 ['19BR0013416544']
MSKU4420970 ['19BR0013246363']
MRKU8494731 ['19BR0013246363']
CMAU4139832 ['19BR0013325034']
MWCU5315644 ['19BR0013051996']
MRKU0699870 ['19BR0013327240']
19BR0013347623 {"canal": "VERDE", "canalBD": 
19BR0012290946 {"canal": "VERDE", "canalBD": 
19BR0013033432 {"canal": "VERDE", "canalBD": 
19BR0013305408 {"canal": "VERDE", "canalBD": 
19BR0013246363 {"canal": "VERDE", "canalBD": 
19BR0013093869 {"canal": "

In [34]:
with open('dues.txt', 'w') as out:
    json.dump(due_detalhe, out)

In [35]:
with open('dues.txt', 'r') as due_in:
    dues_ = json.load(due_in)

In [37]:
dues_['19BR0013347623']

{'canal': 'VERDE',
 'canalBD': 1,
 'chaveAcesso': '19YAX023834561',
 'dataProcessamentoTa': '2019-09-30T18:36:23.000+0000',
 'exportadorEstrangeiro': False,
 'declarantePJBD': '60409075010034',
 'descricaoResultadoProcessarTA': 'Dispensado',
 'despachoEmRecintoAlfandegado': True,
 'embarqueEmRecintoAlfandegado': True,
 'despachoEmRecintoDomiciliar': False,
 'formaExportacao': 'Por conta própria',
 'formaExportacaoBD': 1,
 'id': 2414636,
 'indicadorDAT': False,
 'indicadorExigencia': False,
 'indicadorImpedeEmbarqueTA': 'N',
 'indicadorInspecao': 'N',
 'indicadorOEA': False,
 'informacoesComplementares': '0102EM-008393-19 DESPACHANTES: EDGAR MOTA DA SILVA: REG.8D.06.022 - CPF:080.614.118-22 - DENILSON DIAS DA SILVA: PROC. 11128.726621/2014-19 - CPF 038.471.428-52 - SERGIO MARQUES DE JESUS: PROC. 11128.728458/2014-11 - CPF 080.475.918-94 - GLAUCIA MARA TEIXEIRA: REG.8D.04.026 - CPF 108.285.948-64',
 'usuarioConfaz': False,
 'consultaConfaz': False,
 'listaExigencias': [],
 'listaHistoric

In [38]:
def monta_due_ajna(due):
    def get_dados_recinto(recinto_dict):
        result = {}
        result['codigo'] = recinto_dict.get('codigo')
        depositario = recinto_dict.get('depositario')
        if depositario:
            result['depositario'] = depositario.get('depositario')
            result['nome'] = depositario.get('nome')
            result['descricao'] = depositario.get('descricao')
            unidade = depositario.get('unidadeLocalRFB')
            if unidade:
                unidadeLocalRFB = depositario.get('codigo')

        return result 
    
    keys = ['canal', 'chaveAcesso', 'dataProcessamentoTa', 'descricaoTipoItemDue',
            'exportadorEstrangeiro', 'formaExportacao', 'indicadorOEA', 'informacoesComplementares']
    pacote = {}
    for key in keys:
        item = due.get(key)
        if item is not None:
            pacote[key] = item

    declarante = due.get('niDeclarante')
    if declarante:
        pacote['Declarante'] = declarante.get('numero')
        pacote['Nome Declarante'] = declarante.get('nome')

    destino = due.get('paisImportador')
    if destino:
        pacote['PaisImportador'] = destino.get('nome')

    lista_items = due.get('listaInfoItemDue')
    itensDue = []
    for item in lista_items:
        itemDue = {}
        itemDue['descricaoMercadoria'] = item.get('descricaoMercadoria')
        itemDue['exportadorEstrangeiro'] = item.get('exportadorEstrangeiro')
        ncm = item.get('ncm')
        if ncm:
            itemDue['ncm'] = ncm.get('codigo')
        exportador = item.get('niExportador')
        if exportador:
            itemDue['Exportador'] = exportador.get('numero')
            itemDue['NomeExportador'] = exportador.get('nome')
        itensDue.append(itemDue)
    pacote['itens'] = itensDue
    
    for recinto_tipo in ['recintoAduaneiroDespacho',  'recintoAduaneiroEmbarque']:
        pacote[recinto_tipo] = get_dados_recinto(due.get(recinto_tipo))
    ruc = due.get('ruc')
    if ruc:
        pacote['ruc'] = ruc.get('numero')
    pacote['listaHistorico'] = due.get('listaHistorico')

    return pacote

    


In [40]:
pacote = monta_due_ajna(dues_['19BR0013347623'])
pacote

{'canal': 'VERDE',
 'chaveAcesso': '19YAX023834561',
 'dataProcessamentoTa': '2019-09-30T18:36:23.000+0000',
 'descricaoTipoItemDue': ' Nota Fiscal Eletrônica (NF-e)',
 'exportadorEstrangeiro': False,
 'formaExportacao': 'Por conta própria',
 'indicadorOEA': False,
 'informacoesComplementares': '0102EM-008393-19 DESPACHANTES: EDGAR MOTA DA SILVA: REG.8D.06.022 - CPF:080.614.118-22 - DENILSON DIAS DA SILVA: PROC. 11128.726621/2014-19 - CPF 038.471.428-52 - SERGIO MARQUES DE JESUS: PROC. 11128.728458/2014-11 - CPF 080.475.918-94 - GLAUCIA MARA TEIXEIRA: REG.8D.04.026 - CPF 108.285.948-64',
 'Declarante': '60409075010034',
 'Nome Declarante': 'NESTLE BRASIL LTDA.',
 'PaisImportador': 'SUICA',
 'itens': [{'descricaoMercadoria': 'NESCAFE CLASSIC 12x200g XI',
   'exportadorEstrangeiro': False,
   'ncm': '21011110',
   'Exportador': '60409075010034',
   'NomeExportador': 'NESTLE BRASIL LTDA.'},
  {'descricaoMercadoria': 'NESCAFE CLASSIC 12x200g XI',
   'exportadorEstrangeiro': False,
   'ncm'

In [41]:
pacote_carregamento = {}
for conteiner, numeros_dues in conteineres_listadue.items():
    _id = conteineres_ids[conteiner]
    lista_dues = []
    for due in numeros_dues:
        if due is not None:
            pacote = monta_due_ajna(due_detalhe[due])
            lista_dues.append({'numero': due, **pacote})
    if numeros_dues and len(numeros_dues) > 0:
        pacote_carregamento[_id] = lista_dues
    

In [42]:
pacote_carregamento

{'5d94bbcb9616ee69f69acd0a': [{'numero': '19BR0013347623',
   'canal': 'VERDE',
   'chaveAcesso': '19YAX023834561',
   'dataProcessamentoTa': '2019-09-30T18:36:23.000+0000',
   'descricaoTipoItemDue': ' Nota Fiscal Eletrônica (NF-e)',
   'exportadorEstrangeiro': False,
   'formaExportacao': 'Por conta própria',
   'indicadorOEA': False,
   'informacoesComplementares': '0102EM-008393-19 DESPACHANTES: EDGAR MOTA DA SILVA: REG.8D.06.022 - CPF:080.614.118-22 - DENILSON DIAS DA SILVA: PROC. 11128.726621/2014-19 - CPF 038.471.428-52 - SERGIO MARQUES DE JESUS: PROC. 11128.728458/2014-11 - CPF 080.475.918-94 - GLAUCIA MARA TEIXEIRA: REG.8D.04.026 - CPF 108.285.948-64',
   'Declarante': '60409075010034',
   'Nome Declarante': 'NESTLE BRASIL LTDA.',
   'PaisImportador': 'SUICA',
   'itens': [{'descricaoMercadoria': 'NESCAFE CLASSIC 12x200g XI',
     'exportadorEstrangeiro': False,
     'ncm': '21011110',
     'Exportador': '60409075010034',
     'NomeExportador': 'NESTLE BRASIL LTDA.'},
    {'de

In [43]:
r = requests.post(VIRASANA_URL + "dues/update", json=pacote_carregamento)
print(r.status_code)
print(r.text)


201
{"status":"DUEs inseridas/atualizadas"}

